In [ ]:
# ..... get cluster annotations using Knight-Schrijver celltypes  ..... #

In [2]:
# get list of samples
stages = c(rep('stage23', 2), rep(c('stage28', 'stage32'), each = 3))
samples = c('sample3', 'sample10', 'sample5', 'sample10', 'sample11',
           'sample5', 'sample10', 'sample12')

In [48]:
currstage = 'stage32'
crx = read.delim(paste0(currstage, '_metacell_to_cluster.csv'), sep = ',')
crx[1,]

metacell   cluster   map_type             
1 sample5|26 cluster_1 Reciprocal_auroc_0.95

In [49]:
currsmp = samples[stages==currstage]
mcdf = c()
for(ii in 1:length(currsmp)){
    currsmp1 = currsmp[ii]
    tempmc = read.delim(paste0(currstage, '_', currsmp1, '_metacell.csv'), sep = ',')
    temp = read.delim(paste0(currstage, '_', currsmp1, '_Knight-Schrijver_celltypes.csv'), sep = ',')
    tempmc$stage = currstage
    tempmc$sample = currsmp1    
    tempmc$celltype2 = temp$celltype[match(tempmc$barcode, temp$barcode)]
    mcdf = rbind(mcdf, tempmc)
}
mcdf <- mcdf[!is.na(mcdf$celltype2) & mcdf$celltype2!='unassigned',]
mcdf$metacell_new = paste0(mcdf$sample, '|', mcdf$metacell)
mcdf$cluster = crx$cluster[match(mcdf$metacell_new, crx$metacell)]
mcdf[1:2,]

barcode                            metacell celltype                  
1 stage32_sample5_AAACCCACATACTGTG-1 38       Mural cells               
2 stage32_sample5_AAACCCACATCCTTGC-1  3       MT-enriched cardiomyocytes
  stage   sample  celltype2               metacell_new cluster   
1 stage32 sample5 Endothelial_Capillaries sample5|38   cluster_23
2 stage32 sample5 Cardiomyocytes          sample5|3    cluster_12

In [50]:
# get majority cell type as cluster name; remove Immature_other
cls = unique(crx$cluster)
mcdf$consensus_type = NA
for(ii in 1:length(cls)){
    ids = which(mcdf$cluster==cls[ii])
    tb = table(mcdf$celltype2[ids])
    tb[names(tb)=='Immature_other'] = 0
    cons_cls = names(which.max(tb))
    mcdf$consensus_type[ids] = cons_cls
}
mcdf[1:2,]

barcode                            metacell celltype                  
1 stage32_sample5_AAACCCACATACTGTG-1 38       Mural cells               
2 stage32_sample5_AAACCCACATCCTTGC-1  3       MT-enriched cardiomyocytes
  stage   sample  celltype2               metacell_new cluster   
1 stage32 sample5 Endothelial_Capillaries sample5|38   cluster_23
2 stage32 sample5 Cardiomyocytes          sample5|3    cluster_12
  consensus_type
1 Endocardial   
2 Cardiomyocytes

In [51]:
table(mcdf$consensus_type)


         Cardiomyocytes             Endocardial Endothelial_Capillaries 
                   3980                    2652                     761 
     Endothelial_Venous             Fibroblasts Immature_Cardiomyocytes 
                    136                    3449                    5120 
   Myeloid_Immune_Cells          Neuronal_Cells       Pericytes_Stromal 
                    134                     320                     225 
    Smooth_Muscle_Cells 
                   2783 

In [52]:
# save file
write.table(mcdf, file = paste0(currstage, '_cluster_anno_Knight-Schrijver.csv'),
            sep = ',', row.names = F, col.names = T, quote = F)